In [86]:
!uv add pandas requests openai dotenv openpyxl

Resolved 118 packages in 386ms                                       
Prepared 2 packages in 124ms                                             
Installed 2 packages in 5ms                                 
 + et-xmlfile==2.0.0
 + openpyxl==3.1.5


In [3]:
import os
import dotenv
import openai
import sqlite3
import pandas as pd

dotenv.load_dotenv() # Copy .env.example to .env and fill in the blanks

oai_token = os.getenv("OPENAI_API_KEY")

oai = openai.OpenAI(api_key=oai_token)
onet = sqlite3.connect("onet.database") # Run ./create_onet_database.sh to create it
# This dataset comes from https://epoch.ai/gradient-updates/consequences-of-automating-remote-work
# It contains labels for whethere a O*NET task can be done remotely or not (labeled by GPT-4o)
# You can download it here: https://drive.google.com/file/d/1GrHhuYIgaCCgo99dZ_40BWraz-fzo76r/view?usp=sharing
df_remote_status = pd.read_csv("epoch_task_data.csv")

# BLS OEWS: https://www.bls.gov/oes/special-requests/oesm23nat.zip
df_oesm = pd.read_excel("oesm23national.xlsx")

# Run uv run enrich_task_ratings.py to get this file (trs = Task RatingS)
df_enriched_trs = pd.read_json("task_ratings_enriched.json")

In [4]:
FREQUENCY_MAP = {
    'frequency_category_1': "Yearly or less",
    'frequency_category_2': "More than yearly",
    'frequency_category_3': "More than monthly",
    'frequency_category_4': "More than weekly",
    'frequency_category_5': "Daily",
    'frequency_category_6': "Several times daily",
    'frequency_category_7': "Hourly or more"
}

In [5]:
background_prompt = '''
Estimate the typical duration to complete *one instance* of the following job task from the moment a person starts to work on it to the last moment the person will need to keep it in mind

Take into account that there might be delays between the steps to complete the task, which would lengthen the estimate.

Output a range with the format [duration A] - [duration B] where [duration A] and [duration B] correspond to one of the durations below:
- less than 30 minutes
- 30 minutes
- 1 hour
- 4 hours
- 8 hours
- 16 hours
- 3 days
- 1 week
- 3 weeks
- 6 weeks
- 3 months
- 6 months
- 1 year
- 3 years
- more than 3 year

**Do not output anything besides the range**
'''

In [16]:
df_oesm_detailed = df_oesm[df_oesm['O_GROUP'] == 'detailed'][['OCC_CODE', 'TOT_EMP', 'H_MEAN', 'A_MEAN']].copy()
df_enriched_trs['occ_code_join'] = df_enriched_trs['onetsoc_code'].str[:7]
df = pd.merge(
    df_enriched_trs,
    df_oesm_detailed,
    left_on='occ_code_join',
    right_on='OCC_CODE',
    how='left'
)
df = df.drop(columns=['occ_code_join'])
df

onetsoc_code  task_id  \
0       11-1011.00     8823   
1       11-1011.00     8824   
2       11-1011.00     8827   
3       11-1011.00     8826   
4       11-1011.00     8834   
...            ...      ...   
17634   53-7121.00    12807   
17635   53-7121.00    12804   
17636   53-7121.00    12803   
17637   53-7121.00    12805   
17638   53-7121.00    12810   

                                                    task  \
0      Direct or coordinate an organization's financi...   
1      Confer with board members, organization offici...   
2      Prepare budgets for approval, including those ...   
3      Direct, plan, or implement policies, objective...   
4      Prepare or present reports concerning activiti...   
...                                                  ...   
17634  Unload cars containing liquids by connecting h...   
17635  Clean interiors of tank cars or tank trucks, u...   
17636  Lower gauge rods into tanks or read meters to ...   
17637  Operate conveyors and equipment to transfer gr...   
17638  Perform general warehouse activities, such as ...   

                        occupation_title  \
0                       Chief Executives   
1                       Chief Executives   
2                       Chief Executives   
3                       Chief Executives   
4                       Chief Executives   
...                                  ...   
17634  Tank Car, Truck, and Ship Loaders   
17635  Tank Car, Truck, and Ship Loaders   
17636  Tank Car, Truck, and Ship Loaders   
17637  Tank Car, Truck, and Ship Loaders   
17638  Tank Car, Truck, and Ship Loaders   

                                  occupation_description  \
0      Determine and formulate policies and provide o...   
1      Determine and formulate policies and provide o...   
2      Determine and formulate policies and provide o...   
3      Determine and formulate policies and provide o...   
4      Determine and formulate policies and provide o...   
...                                                  ...   
17634  Load and unload chemicals and bulk solids, suc...   
17635  Load and unload chemicals and bulk solids, suc...   
17636  Load and unload chemicals and bulk solids, suc...   
17637  Load and unload chemicals and bulk solids, suc...   
17638  Load and unload chemicals and bulk solids, suc...   

       frequency_category_1  frequency_category_2  frequency_category_3  \
0                      5.92                 15.98                 29.68   
1                      1.42                 14.44                 27.31   
2                     15.50                 38.21                 32.73   
3                      3.03                 17.33                 20.30   
4                      1.98                 14.06                 42.60   
...                     ...                   ...                   ...   
17634                  6.05                 29.21                  6.88   
17635                  1.47                  6.33                 21.70   
17636                  4.52                  1.76                  4.65   
17637                  6.97                 12.00                  2.52   
17638                  5.91                 10.85                  6.46   

       frequency_category_4  frequency_category_5  frequency_category_6  \
0                     21.18                 19.71                  4.91   
1                     25.52                 26.88                  2.52   
2                      5.15                  5.25                  0.19   
3                     18.10                 33.16                  2.01   
4                     21.24                 13.18                  6.24   
...                     ...                   ...                   ...   
17634                 13.95                 27.65                  7.93   
17635                 25.69                 32.35                 12.47   
17636                 17.81                 37.42                 23.31   
17637      

In [11]:
df_merged = pd \
    .merge(left=df_enriched_trs, right=df_remote_status[['O*NET-SOC Code', 'Remote']], how='left', left_on='onetsoc_code', right_on='O*NET-SOC Code') \
    .drop(columns=['O*NET-SOC Code']) \
    .rename(columns={'Remote': 'remote'}) \
    .rename(columns=FREQUENCY_MAP) \
    .query('remote == "remote" and importance_average >= 3 and relevance_average > 50')

row = df_merged.iloc[30000]
print('Task: ', row['task'])
print('Occupation Description: ', row['occupation_description'])
print('Occupation Title: ', row['occupation_title'])

len(df_merged)

Task:  Identify, evaluate and recommend hardware or software technologies to achieve desired database performance.
Occupation Description:  Design strategies for enterprise databases, data warehouse systems, and multidimensional networks. Set standards for database operations, programming, query processes, and security. Model, design, and construct large relational databases or data warehouses. Create and optimize data models for warehouse infrastructure and workflow. Integrate new systems with existing warehouse structure and refine system performance and functionality.
Occupation Title:  Database Architects


119976

In [ ]:
# Cross-reference woth BLS OEWS
# It doesn't really make sens to have it per-task, we only need it per-occupation...
df_oesm_detailed = df_oesm[df_oesm['O_GROUP'] == 'detailed'][['OCC_CODE', 'TOT_EMP', 'H_MEAN', 'A_MEAN']].copy()
df_merged['occ_code_join'] = df_merged['onetsoc_code'].str[:7]
df_merged = pd.merge(
    df_merged,
    df_oesm_detailed,
    left_on='occ_code_join',
    right_on='OCC_CODE',
    how='left'
)
df_merged = df_merged.drop(columns=['occ_code_join'])
df_merged

In [76]:
response = oai.chat.completions.create(messages=[{"role": "user", "content": "Tell me a joke"}], model="gpt-4.1-2025-04-14", max_tokens=100, temperature=0.7, n=1, stop=None)
joke = response.choices[0].message.content.strip()
print(joke)

Why did the scarecrow win an award?

Because he was outstanding in his field!
